In [1]:
import pandas as pd
import numpy as np
import ast
from sklearn.preprocessing import OneHotEncoder
pd.set_option('max.columns',200)

In [2]:
# load data
city = pd.read_csv('../data/raw/worldcities.csv')
madrid = pd.read_csv('../data/raw/madrid.csv')
london = pd.read_csv('../data/raw/london.csv')
paris = pd.read_csv('../data/raw/paris.csv')

In [3]:
# select relevant cities
city_df = city[city['id'].astype('str').isin(['1250015082', '1826645935', '1724616994'])]
city_df = city_df.rename(columns={'id':'city_id', 'city':'city_name'})
city_df['city_id'] = city_df['city_id'].astype('str')
bnb_city_id = {'Paris':'1250015082', 'London':'1826645935', 'Madrid':'1724616994'}

In [4]:
madrid['city'] = 'Madrid'
london['city'] = 'London'
paris['city'] = 'Paris'

In [5]:
madrid['city_id'] = madrid['city'].map(bnb_city_id)
london['city_id'] = london['city'].map(bnb_city_id)
paris['city_id'] = paris['city'].map(bnb_city_id)

In [6]:
city_df = city_df[['city_id', 'lat', 'lng']]

In [7]:
madrid = pd.merge(madrid, city_df, how='left', on='city_id')
london = pd.merge(london, city_df, how='left', on='city_id')
paris = pd.merge(paris, city_df, how='left', on='city_id')

## Feature Engineering

#### Impute bathrooms with bathroom text

In [8]:
bathroom_text_dict = {'Shared half-bath': '0.5', 'Half-bath': '0.5', 'Private half-bath': '0.5', np.nan: '1'}

In [9]:
madrid['bathrooms_text'] = madrid['bathrooms_text'].apply(lambda x: bathroom_text_dict[x] if x in list(bathroom_text_dict.keys()) else x)
madrid['bathrooms'] = madrid['bathrooms_text'].apply(lambda x: float(x.split()[0]))

In [10]:
london['bathrooms_text'] = london['bathrooms_text'].apply(lambda x: bathroom_text_dict[x] if x in list(bathroom_text_dict.keys()) else x)
london['bathrooms'] = london['bathrooms_text'].apply(lambda x: float(x.split()[0]))

In [11]:
paris['bathrooms_text'] = paris['bathrooms_text'].apply(lambda x: bathroom_text_dict[x] if x in list(bathroom_text_dict.keys()) else x)
paris['bathrooms'] = paris['bathrooms_text'].apply(lambda x: float(x.split()[0]))

#### Distance of Airbnb to city center


In [12]:
from geopy import distance

def dist_city_center(prop_lat, prop_lon, city_lat, city_lon):
    prop_coords = (prop_lat, prop_lon)
    city_coords = (city_lat, city_lon)
    dist = distance.great_circle(prop_coords, city_coords).kilometers
    print(dist)
    return dist


In [13]:
madrid['cc_dist'] = madrid.apply(lambda x: dist_city_center(x.latitude, x.longitude, x.lat, x.lng), axis=1)
london['cc_dist'] = london.apply(lambda x: dist_city_center(x.latitude, x.longitude, x.lat, x.lng), axis=1)
paris['cc_dist'] = paris.apply(lambda x: dist_city_center(x.latitude, x.longitude, x.lat, x.lng), axis=1)

4.44869619346421
4.487254305733764
3.553994098085121
1.0774570486726431
0.49974890250993376
3.2337710699240514
3.4008138533029086
1.0483303830219488
1.2588789349033258
1.6014158895793966
0.4674923654524423
1.0727601108809117
1.6554305526206003
1.7512905027923964
0.6195567268439395
7.699343621980097
1.532163335053543
0.983472784650266
1.5998023455177643
1.3465342181602107
1.608017524014534
1.3517575589671174
0.9044674220902241
1.6105117033249114
1.1813275092981428
1.9903281442187342
0.6608507636445311
1.047182054064715
5.019781273487587
9.313212390842681
1.507264936052313
4.395141971100127
0.6859732446795778
2.1439819109714433
2.1581420903656507
1.8794676529854781
1.6778755122220128
1.2902556181930347
1.6186764321760996
1.026572170235799
0.91086008539327
6.854380324792891
1.5692979132204805
0.9140496399706226
2.2391192290917186
5.4108049472929425
1.2301949580241973
1.648121980001249
1.3638215929542639
1.5204999670986177
1.3504570985372981
1.8451425806069643
1.3260180980032232
1.09238670

0.6042266271495214
2.9527797927570107
3.0520983334754015
1.719709285656831
1.3164620643761509
2.35433709928132
0.9436368752580085
2.16883051925255
9.722924754210934
0.8502195211324889
0.5904107652585399
0.9576729893710424
1.6193143102046639
1.7146961679064725
0.9241976444840875
1.7825475198259213
2.1045126748942864
1.1181820097192008
2.4569113286581103
1.8022589044419657
0.9331934090644709
5.838703615823354
0.8562087276382113
0.9977365955883285
3.649233779183868
1.1922744466217192
1.2102858491912265
1.67749031307776
1.7024397830841365
1.990158648388688
0.9897343062402771
3.2344933970485235
1.1243069643407388
1.160491817271997
2.370951995376781
1.2572589474941471
1.9857701988124399
0.5371287162495622
1.294403159961492
0.9302178181521162
3.521418167056892
0.5231671847849768
1.5730893988884826
1.7217400420481939
1.0944010032403075
1.1072456025311022
1.0208771202917803
1.0752550791109006
1.21992725011691
2.4768602688621644
1.2876368638593596
3.80919006586516
1.3775056885116481
3.7002100330

2.8842848239361354
5.932249942053744
1.5114396117242903
10.802457081762684
3.8783543312061255
0.8733508650163632
1.8448179371469584
0.21963940467494708
10.345246306469999
4.823095566415948
2.3912141164150476
1.9669359729611804
2.1511203380358954
0.6507303498142073
1.2643503959822076
2.8293261632655926
1.9939551007587832
1.111667140437181
7.808030803011862
3.017795905197054
3.7202823624184083
2.824584166688341
1.167282442941942
1.0727586096555677
2.4345684663314704
1.4403581113514514
2.0158755723826203
1.2827458217798253
1.3989449481202765
1.6492967570814197
2.290570108543808
2.5810616829386617
1.62987555195486
1.083192316300378
0.7043007392499969
1.7585819771824234
3.6684666671990893
1.067270680669055
0.7216599210266524
2.443219863152516
2.0547706979420766
9.022753479298974
1.7362293313573565
2.9524419727068456
1.3270083699683446
3.6666574689874123
1.3200615864473129
1.4713481909582093
0.37087321760310865
1.2848881024048702
4.1350446341730756
3.5424472572781056
1.199333933540059
3.2142

1.8251102207344947
2.768044629206916
4.517390276129205
5.206900247664477
1.0033478761431387
1.746694947597618
3.154098213336061
1.173056108970238
1.2664809161878734
2.9599580507402283
4.316247888871193
1.5046624424797261
3.654623303170275
1.8994476548862589
1.4062289792012639
2.28132839205321
3.562704675584941
1.6369086603482044
1.8306134701348704
2.015602489055911
1.4450660810524627
5.89124638413712
5.713466345416186
10.690632821431587
2.7814791883784133
2.78686533644581
0.9402386863183314
2.0366110190010063
1.718633194360352
4.262304161898952
6.5785114902735415
0.7424421743928104
2.1605815057063795
1.0906615663940684
4.601666163865296
1.534959879652797
1.0466364524733116
1.1121751685176815
0.39100507880618596
3.0387821794211414
5.026852024123277
1.4226737622871353
0.7332618891545172
1.049129186364046
0.9406105765561176
0.9884091053835223
0.7581373128160798
2.8418713234549497
0.9194111753537377
1.1964793025246931
1.4765798270508548
1.9392277277934784
0.55523647737135
1.40955932939751


2.133883384530932
1.0718658088501054
1.8390212136513913
1.421019081854704
2.033622751379118
3.935545603773976
2.992012686349146
1.3507374717701173
2.9065850337807686
0.9730302106789748
0.5643010885410507
1.0292498829992127
1.2938827244318103
1.525966040505876
1.6554305526205453
9.979359791499967
3.0136807562714174
6.049989389631395
1.332328989160347
3.0828184170871626
2.1377365879774435
1.6791791711816255
0.5855275712678736
1.5568902770439128
1.700941040351949
0.90730920210156
1.6181393663952786
3.6872494372952387
4.4190246499581685
1.4513100209450627
1.1435453174665127
0.8370802184185487
2.0170901911992276
1.2836182231023714
1.6542122180214756
2.1601593489221322
1.0813908695269296
2.374375566782241
4.400091568361383
2.139160038036735
0.9751887647600868
3.8310731995138267
2.6628863490163375
1.0225165098776565
2.643953372681843
5.092058654849007
2.3743984278068835
2.372492969425353
3.9674074571508013
1.7797128606076673
4.030262591031248
3.537084476774248
2.5216841483193524
1.98943776446

...

3.8544795916311925
4.349573098485064
3.9493971816065976
7.168138473049018
3.7666927473280465
3.0840482572690413
2.833649964010778
3.4924325727676107
0.6970462044376
3.770499928178636
3.785844367604983
1.4019949778961838
0.9497510116895177
5.028949672771179
1.427286445386748
3.052816106746781
4.038297736863441
5.038640160594856
3.594048977238032
2.590229824220396
2.1279930986276008
2.4329914099073386
1.2446214230672283
2.382941646845571
0.9294805077898359
4.175657779247847
1.2675951220057091
4.867096182486948
2.175510648859836
3.161661888648035
0.7498797303774645
2.964825545332997
4.491275556942067
3.6749050798134433
2.5351806330496
4.084773861353044
3.1849731397364387
0.9264134653758977
1.435740378570056
1.045955497156093
1.4145947341521667
2.8320169467724825
1.2166995154844404
3.1231797713820497
1.2853387339660045
1.4186226173765684
4.807456240680515
2.301268161751763
2.656337052908399
1.6660356278245694
1.3599865131624642
2.266548498916049
3.7890930984589954
3.2933740845157047
1.8469

0.9247054368246799
4.278412190331151
3.0444124179268943
3.9787231022314264
2.953922385938579
3.499576434320403
0.7543783279294065
1.4882311741562575
3.1830062442318776
4.233843990786029
3.4869942069509614
1.1801713915429881
1.2378366950148456
1.3508003287543517
3.092762491564346
3.569579811228647
5.488568120468579
5.288046437922335
5.401060361101403
5.396086519435009
5.354146685732538
3.5180051907607055
5.314973281230795
2.6189297799941866
1.1811746476561757
4.568121577432362
5.634545357648198
7.081906744377374
5.648800672944795
2.486125890157922
3.176749892501332
4.2488548041276815
2.1852960310801737
2.60456828874314
2.359200757122958
3.4305147070472506
2.868793642330862
4.1853306423191174
6.987755174640019
1.4876205970757688
3.2179840112030766
4.346787035521873
2.7200517775488096
3.4823809549516027
0.9279584669819394
2.292041753795163
4.376806479110804
4.573462717191166
1.427343770960925
1.56437128248865
7.198253246138858
4.06114447666716
7.086419652215725
7.200325324800737
6.1236233

3.7317324721552696
3.545081714394202
4.653322129079538
2.6871257134232374
5.599024855980475
4.107262692327016
4.088899056430093
4.159968008456453
2.5748703261319403
4.448403466467977
1.3827182360450847
4.762871863895158
5.198378610805687
0.7729138052930802
3.730263327069174
3.2016410041019485
1.9330307197047165
2.574027166747043
2.320711271772189
2.601668903972514
1.5022016666951286
1.022344605805836
1.0733207781121752
1.4624701898563899
2.22256059563346
2.3389582301026586
2.061717986541753
5.129828493651421
4.4973629550208445
2.5671378657959236
0.6535636970290024
2.120373627538394
1.6282133454885679
3.7358601599627357
0.8101377450859455
5.101334643544044
2.049804331351395
2.241630152268291
3.14815423210246
1.8910863423954511
0.8101377450859455
0.8101377450859455
0.8101377450859455
2.070753976679806
0.6129875444848106
3.102280734611597
2.51626192205126
1.7312932007598323
1.6269871592754244
4.01164948148708
4.298990546492874
3.219306532889559
4.115623187148615
3.3636657169884017
1.24823

3.543559800661888
4.594330745685808
0.6218579747595538
3.635079883424825
5.169433972485756
1.3130634986889933
2.609625700967762
3.8911392881247293
3.0058905373963793
1.577871010777187
2.549260758157272
1.7885069988226738
3.7898718405855907
1.9243112066702028
2.1058809648501424
3.066924579744214
2.4121790520507047
0.8768410958225165
3.114068915128304
2.6752004957013424
4.270440978828905
5.76691227690521
4.469603257021949
4.426138237578312
1.1003357135878544
1.8973204457836912
3.918845929199503
2.5083971181246008
4.953523824868241
2.519981110038976
4.869089311481662
1.541384786693421
2.552334006487437
2.6493400660205397
3.589794394136796
1.8060109690510768
1.841307239991756
6.194213646110282
0.8802315877922627
4.172420515298564
4.664627579804208
3.0679853478045285
4.049073716918025
1.417838161238559
4.674337283562767
1.7647089459813015
3.1146616353798544
1.9885807821583232
5.08394723258259
0.45580078003177443
2.3608002476573233
2.2058559439811614
1.0272271633367966
3.9675837239012925
4.5

6.447537262914943
1.4209068862883103
2.2150320626882394
1.3190470018750435
3.2641437392110997
1.9478481262919498
3.2061881638778553
4.263360349957898
3.54093518015916
3.629650465886125
2.6871472506964915
1.6039150572079928
2.1131934615620334
5.753662198937704
2.1369433467268744
4.569002027274236
3.324444904998251
3.506953100106756
2.132540910082673
2.1325854655453313
2.1613677849245216
2.282764334176309
2.2869174388172437
3.2142087298120283
1.776642145869342
1.8180545467990605
5.40779923790478
4.884841876239035
2.8576951811878573
2.0761192867642886
4.942470030448644
0.7588600215424839
5.156509356851447
0.9816764503960078
1.1239341641730571
6.183911484615699
3.7419500020902925
2.9450814187559247
1.6794557775050103
2.0543544894115913
8.136896091117055
3.7336597236896893
3.766607399832098
3.7825849126261595
3.3460551374942615
3.773651195056591
4.450276744023541
5.123226889515274
0.7366928461734206
4.381527539713592
6.372465888794047
6.369528045648617
2.2453749282272875
1.7578114234626372


In [14]:
def haversine_np(lon1, lat1, lon2, lat2):
    """
    Calculate the great circle distance between two points
    on the earth (specified in decimal degrees)

    All args must be of equal length.    

    """
    lon1, lat1, lon2, lat2 = map(np.radians, [lon1, lat1, lon2, lat2])

    dlon = lon2 - lon1
    dlat = lat2 - lat1

    a = np.sin(dlat/2.0)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon/2.0)**2

    c = 2 * np.arcsin(np.sqrt(a))
    km = 6367 * c
#     m = km * 0.621371
    
    return km

In [15]:
def num_close_airbnbs(y, df, dist_thresh):
    df['cur_lat'] = y.latitude
    df['cur_lon'] = y.longitude
    df['rel_dist'] = haversine_np(df['cur_lon'], df['cur_lat'], df['longitude'], df['latitude'])
    num_close = np.sum(np.where(df['rel_dist'] <= dist_thresh, 1, 0)) - 1
    return num_close

In [16]:
# takes ~10 mins to run
df = madrid.copy()
madrid['num_bnb_1km'] = madrid.apply(lambda y: num_close_airbnbs(y, df, 1), axis=1)


In [17]:
df = london.copy()
london['num_bnb_1km'] = london.apply(lambda y: num_close_airbnbs(y, df, 1), axis=1)


In [18]:
df = paris.copy()
paris['num_bnb_1km'] = paris.apply(lambda y: num_close_airbnbs(y, df, 1), axis=1)


#### Description & Name Length

In [19]:
# create length of description
madrid['desc_len'] = madrid['description'].str.len()
london['desc_len'] = london['description'].str.len()
paris['desc_len'] = paris['description'].str.len()

# create length of name
madrid['name_len'] = madrid['name'].str.len()
london['name_len'] = london['name'].str.len()
paris['name_len'] = paris['name'].str.len()

#### Ratio of Bedrooms to bathrooms

In [20]:
madrid['bathrooms'].fillna(madrid['bathrooms'].mode()[0], inplace=True)
madrid['bedrooms'].fillna(madrid['bedrooms'].mode()[0], inplace=True)
madrid['beds'].fillna(madrid['beds'].mode()[0], inplace=True)

london['bathrooms'].fillna(london['bathrooms'].mode()[0], inplace=True)
london['bedrooms'].fillna(london['bedrooms'].mode()[0], inplace=True)
london['beds'].fillna(london['beds'].mode()[0], inplace=True)

paris['bathrooms'].fillna(paris['bathrooms'].mode()[0], inplace=True)
paris['bedrooms'].fillna(paris['bedrooms'].mode()[0], inplace=True)
paris['beds'].fillna(paris['beds'].mode()[0], inplace=True)

In [21]:
madrid['bed_bath_ratio'] = round(madrid.bedrooms/madrid.bathrooms,2)
london['bed_bath_ratio'] = round(london.bedrooms/london.bathrooms,2)
paris['bed_bath_ratio'] = round(paris.bedrooms/paris.bathrooms,2)

#### How long has the host been hosting

In [22]:
madrid['today'] = '2021-04-01'
london['today'] = '2021-04-01'
paris['today'] = '2021-04-01'

In [23]:
madrid['host_since'] = pd.to_datetime(madrid['host_since'])
madrid['today'] = pd.to_datetime(madrid['today'])
madrid['years_of_hosting'] = round(((madrid['today'] - madrid['host_since']).dt.days)/365,1)

london['host_since'] = pd.to_datetime(london['host_since'])
london['today'] = pd.to_datetime(london['today'])
london['years_of_hosting'] = round(((london['today'] - london['host_since']).dt.days)/365,1)

paris['host_since'] = pd.to_datetime(paris['host_since'])
paris['today'] = pd.to_datetime(paris['today'])
paris['years_of_hosting'] = round(((paris['today'] - paris['host_since']).dt.days)/365,1)

#### Years since last review (benchmark date = 2021-04-01)

In [24]:
madrid['last_review'] = pd.to_datetime(madrid['last_review'])
madrid['years_since_lastreview'] = round(((madrid['today'] - madrid['last_review']).dt.days)/365,1)

london['last_review'] = pd.to_datetime(london['last_review'])
london['years_since_lastreview'] = round(((london['today'] - london['last_review']).dt.days)/365,1)

paris['last_review'] = pd.to_datetime(paris['last_review'])
paris['years_since_lastreview'] = round(((paris['today'] - paris['last_review']).dt.days)/365,1)

In [25]:
# Dropping the column I made to get the dates
madrid.drop('today', axis=1, inplace=True)
london.drop('today', axis=1, inplace=True)
paris.drop('today', axis=1, inplace=True)

In [26]:
# null values generated because there is no 'last_review'
print(madrid.years_since_lastreview.isnull().sum())
print(london.years_since_lastreview.isnull().sum())
print(paris.years_since_lastreview.isnull().sum())

5975
22194
15462


#### Change % to float for column 'host_response_rate'

In [27]:
madrid['host_response_rate'] = madrid['host_response_rate'].str.rstrip('%').astype('float')
london['host_response_rate'] = london['host_response_rate'].str.rstrip('%').astype('float')
paris['host_response_rate'] = paris['host_response_rate'].str.rstrip('%').astype('float')

In [28]:
madrid.shape

(20156, 85)

#### Column 'host_has_profile_pic', 'host_since', 'host_identity_verified' all has 203 missing values

In [29]:
# Let's change all nan values to 'f' (no profile pic, identity not verified)
madrid.loc[madrid['host_has_profile_pic'].isnull(), 'host_has_profile_pic'] = 'f'
madrid.loc[madrid['host_identity_verified'].isnull(), 'host_identity_verified'] = 'f'

london.loc[london['host_has_profile_pic'].isnull(), 'host_has_profile_pic'] = 'f'
london.loc[london['host_identity_verified'].isnull(), 'host_identity_verified'] = 'f'

paris.loc[paris['host_has_profile_pic'].isnull(), 'host_has_profile_pic'] = 'f'
paris.loc[paris['host_identity_verified'].isnull(), 'host_identity_verified'] = 'f'

#### Encode 'thumbnail_url' column to 1 or 0 (if you have thumbnail then 1 else 0)

In [30]:
# we won't using this as dummy variable
madrid.host_thumbnail_url.nunique()

london.host_thumbnail_url.nunique()

paris.host_thumbnail_url.nunique()

51711

In [31]:
# If the value is not null, then we assign 1, else 0
madrid.loc[madrid['host_thumbnail_url'].notnull(), 'host_thumbnail_url'] = 1

london.loc[london['host_thumbnail_url'].notnull(), 'host_thumbnail_url'] = 1

paris.loc[paris['host_thumbnail_url'].notnull(), 'host_thumbnail_url'] = 1


In [32]:
madrid.loc[madrid['host_thumbnail_url'].isnull(), 'host_thumbnail_url'] = 0

london.loc[london['host_thumbnail_url'].isnull(), 'host_thumbnail_url'] = 0

paris.loc[paris['host_thumbnail_url'].isnull(), 'host_thumbnail_url'] = 0

In [33]:
# Now we have either 1 or 0
madrid.host_thumbnail_url.unique()


array([1, 0], dtype=object)

#### Drop duplicate rows

In [34]:
duplicate_rows_madrid = madrid[madrid.duplicated()]
print('Madrid number of duplicate rows:', duplicate_rows_madrid.shape)

duplicate_rows_london = london[london.duplicated()]
print('Madrid number of duplicate rows:', duplicate_rows_london.shape)

duplicate_rows_paris = paris[paris.duplicated()]
print('Madrid number of duplicate rows:', duplicate_rows_paris.shape)

#drop the duplicate rows
madrid = madrid.drop_duplicates()

london = london.drop_duplicates()

paris = paris.drop_duplicates()

Madrid number of duplicate rows: (0, 85)
Madrid number of duplicate rows: (0, 85)
Madrid number of duplicate rows: (0, 85)


#### Number of Beds to bedroom ratio

In [35]:
madrid['bed_bath_ratio'] = round(madrid.bedrooms/madrid.bathrooms,2)
london['bed_bath_ratio'] = round(london.bedrooms/madrid.bathrooms,2)
paris['bed_bath_ratio'] = round(paris.bedrooms/madrid.bathrooms,2)

In [36]:
# There are null values in 'bed_bath_ratio' because there are houses with no bathrooms (campers, private rooms..)
# Replace null values in 'bed_bath_ratio' with 0
madrid.loc[madrid['bed_bath_ratio'].isnull(), 'bed_bath_ratio'] = 0.00
london.loc[london['bed_bath_ratio'].isnull(), 'bed_bath_ratio'] = 0.00
paris.loc[paris['bed_bath_ratio'].isnull(), 'bed_bath_ratio'] = 0.00

#### Make host_has_profile_pic, host_identity_verified, instant_bookable

In [37]:
madrid['host_has_profile_pic'] = np.where(madrid.host_has_profile_pic=='t',1,0)
madrid['host_identity_verified'] = np.where(madrid.host_identity_verified=='t',1,0)
madrid['instant_bookable'] = np.where(madrid.instant_bookable=='t',1,0)

london['host_has_profile_pic'] = np.where(london.host_has_profile_pic=='t',1,0)
london['host_identity_verified'] = np.where(london.host_identity_verified=='t',1,0)
london['instant_bookable'] = np.where(london.instant_bookable=='t',1,0)

paris['host_has_profile_pic'] = np.where(paris.host_has_profile_pic=='t',1,0)
paris['host_identity_verified'] = np.where(paris.host_identity_verified=='t',1,0)
paris['instant_bookable'] = np.where(paris.instant_bookable=='t',1,0)

#### Make log price

In [38]:
# make response for madrid
madrid['price'] = madrid['price'].str.replace(',', '')
madrid['price'] = madrid['price'].str.replace('$', '')
madrid['price'] = madrid['price'].astype(float)
madrid = madrid[madrid['price']>0].reset_index(drop=True)
madrid['log_price'] = np.log(madrid['price'])

# make response for london
london['price'] = london['price'].str.replace(',', '')
london['price'] = london['price'].str.replace('$', '')
london['price'] = london['price'].astype(float)
london = london[london['price']>0].reset_index(drop=True)
london['log_price'] = np.log(london['price'])

# make response for paris
paris['price'] = paris['price'].str.replace(',', '')
paris['price'] = paris['price'].str.replace('$', '')
paris['price'] = paris['price'].astype(float)
paris = paris[paris['price']>0].reset_index(drop=True)
paris['log_price'] = np.log(paris['price'])

/Users/nikhilbhargava/opt/anaconda3/envs/mids-python/lib/python3.7/site-packages/ipykernel_launcher.py:3: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will*not* be treated as literal strings when regex=True.
  This is separate from the ipykernel package so we can avoid doing imports until
/Users/nikhilbhargava/opt/anaconda3/envs/mids-python/lib/python3.7/site-packages/ipykernel_launcher.py:10: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will*not* be treated as literal strings when regex=True.
  # Remove the CWD from sys.path while we load stuff.
/Users/nikhilbhargava/opt/anaconda3/envs/mids-python/lib/python3.7/site-packages/ipykernel_launcher.py:17: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expression

#### Filter on needed columns

In [39]:
filter_cols = ['log_price',
 'accommodates',
 'bathrooms',
 'host_has_profile_pic',
 'host_identity_verified',
 'host_response_rate',
 'instant_bookable',
 'number_of_reviews',
 'review_scores_rating',
 'host_thumbnail_url',
 'bedrooms',
 'beds',
 'cc_dist',
 'num_bnb_1km',
 'desc_len',
 'name_len',
 'bed_bath_ratio',
 'years_of_hosting',
 'years_since_lastreview',
 'amenities',
 'property_type',
 'room_type']

In [40]:
madrid = madrid[filter_cols]
madrid = madrid.rename(columns={'host_thumbnail_url':'thumbnail_url'})

london = london[filter_cols]
london = london.rename(columns={'host_thumbnail_url':'thumbnail_url'})

paris = paris[filter_cols]
paris = paris.rename(columns={'host_thumbnail_url':'thumbnail_url'})

#### Amenities

In [41]:
def handle_entry(s):
    # return amenities list
    s_list = ast.literal_eval(s)
    s_list = [s.lower() for s in s_list]
    return s_list

In [42]:
madrid['amenities'] = madrid['amenities'].apply(lambda x: handle_entry(x))
london['amenities'] = london['amenities'].apply(lambda x: handle_entry(x))
paris['amenities'] = paris['amenities'].apply(lambda x: handle_entry(x))

In [43]:
amenity_dict = {'amenity_tv': ['cable tv','tv'], 
 'amenity_baby': ['baby bath','baby monitor', 'babysitter recommendations', 'changing table', 
                  "children’s books and toys", "children’s dinnerware", 'family/kid friendly',
                  'fireplace guards', 'crib', 'high chair', "pack ’n play/travel crib", 'table corner guards',
                  'outlet covers', 'stair gates'],
'amenity_bed': ['bed linens', "extra pillows and blankets",'firm mattress','firm matress','firm mattress'],
'amenity_accessibility': [' smooth pathway to front door','accessible-height bed','accessible-height toilet',
                          'disabled parking spot','fixed grab bars for shower & toilet','flat smooth pathway to front door',
                          'grab-rails for shower and toilet','ground floor access','handheld shower head',
                          'path to entrance lit at night','roll-in shower with chair','step-free access',
                          'well-lit path to entrance','wheelchair accessible','wide clearance to bed',
                          'wide clearance to shower & toilet','wide clearance to shower and toilet','wide doorway',
                          'wide entryway','wide hallway clearance'],
'amenity_aircondition': ['air conditioning'],
'amenity_bbqgrill': ['bbq grill'], 
'amenity_breakfast': ['breakfast'],
'amenity_buzzer_wireless_intercom':['buzzer/wireless intercom'],
'amenity_cleaning_bf_checkout': ['cleaning before checkout'],
'amenity_pets': ['cat(s)', 'dog(s)', 'other pet(s)', 'pets allowed', 'pets live on this property'],
'amenity_washer_dryer':['dryer','washer','washer / dryer'],
'amenity_ev_charger':['ev charger'],
'amenity_elevator':['elevator','elevator in building'],
'amenity_free_park':['free parking on premises','free parking on street'],
'amenity_game':['game console'],
'amenity_indoor_fireplace': ['indoor fireplace'],
'amenity_gym':['gym'],
'amenity_clothes':['iron', 'hangers'],
'amenity_essential':['essentials'],
'amenity_hot_water': ['hot water'],
'amenity_garden_backyard':['garden or backyard'],
'amenity_bathroom':['bath towel', 'hand or paper towel', 'toilet paper', 'hand soap', 'body soap', 
                    'bathtub', 'shampoo', 'bathtub with shower chair', 'hot tub', 'shampoo', 'hair dryer'],
'amenity_host_greet': ['host greets you'], 
'amenity_heating': ['heating'],
'amenity_kitchen': ['refrigerator', 'dishes and silverware', 'microwave', 'hot water kettle', 
                    'dishwasher', 'coffee maker', 'stove', 'oven', 'cooking basics'],
'amenity_lake': ['lake access'],
'amenity_work': ['laptop friendly workspace'],
'amenity_bedroom_lock': ['lock on bedroom door'],
'amenity_lockbox': ['lockbox', 'keypad'],
'amenity_longterm_stays': ['long term stays allowed'],
'amenity_luggage_dropoff': ['luggage dropoff allowed'],
'amenity_other': ['other'],
'amenity_paid_parking': ['paid parking off premises'],
'amenity_patio_balcony': ['patio or balcony'],
'amenity_wifi': ['pocket wifi', 'wireless internet', 'internet', 'ethernet connection', 'internet'],
'amenity_pool': ['pool'],
'amenity_privacy': ['private bathroom', 'private entrance', 'private living room', 'room-darkening shades'],
'amenity_safety': ['safety card', 'smart lock', 'smartlock', 'smoke detector', 
                   'fire extinguisher', 'first aid kit', 'window guards'],
'amenity_self_checkin': ['self check-in'],
'amenity_single_level_home': ['single level home'],
'amenity_smoking_allowed': ['smoking allowed'],
'amenity_suitable_for_events': ['suitable for events'],
'amenity_waterfront': ['waterfront'],
'amenity_window_guards': ['window guards'],
'amenity_self_checkin':['self check-in'],
'amenity_beach_essentials':['beach essentials'],
'amenity_beach_front':['beachfront'],
'amenity_doorman':['doorman','doorman entry'],
'amenity_24hour_checkin':['24-hour check-in']}

In [44]:
def ohe_amenities(amenity, x):
    if amenity in x:
        return 1
    else:
        return 0

In [45]:
# madrid amenities
for agroup in amenity_dict.keys():
    amenity_cols = amenity_dict[agroup]
    for amenity in amenity_cols:
        madrid[amenity] = madrid['amenities'].apply(lambda x: ohe_amenities(amenity, x))
    madrid[agroup] = madrid[amenity_cols].sum(axis=1)
    madrid = madrid.drop(columns=amenity_cols)
    madrid[agroup] = np.where(madrid[agroup] >= 1, 1, 0)

In [46]:
# london amenities
for agroup in amenity_dict.keys():
    amenity_cols = amenity_dict[agroup]
    for amenity in amenity_cols:
        london[amenity] = london['amenities'].apply(lambda x: ohe_amenities(amenity, x))
    london[agroup] = london[amenity_cols].sum(axis=1)
    london = london.drop(columns=amenity_cols)
    london[agroup] = np.where(london[agroup] >= 1, 1, 0)

In [47]:
# paris amenities
for agroup in amenity_dict.keys():
    amenity_cols = amenity_dict[agroup]
    for amenity in amenity_cols:
        paris[amenity] = paris['amenities'].apply(lambda x: ohe_amenities(amenity, x))
    paris[agroup] = paris[amenity_cols].sum(axis=1)
    paris = paris.drop(columns=amenity_cols)
    paris[agroup] = np.where(paris[agroup] >= 1, 1, 0)

In [48]:
# drop remaining columns
madrid = madrid.drop(columns=['amenities'])
london = london.drop(columns=['amenities'])
paris = paris.drop(columns=['amenities'])

#### Impute Null Values

In [49]:
# impute madrid null values
madrid['host_response_rate'] = madrid['host_response_rate'].fillna(np.mean(madrid['host_response_rate']))
madrid['review_scores_rating'] = madrid['review_scores_rating'].fillna(np.mean(madrid['review_scores_rating']))
madrid['desc_len'] = madrid['desc_len'].fillna(np.mean(madrid['desc_len']))
madrid['name_len'] = madrid['name_len'].fillna(np.mean(madrid['name_len']))
madrid['years_since_lastreview'] = madrid['years_since_lastreview'].fillna(np.mean(madrid['years_since_lastreview']))
madrid['years_of_hosting'] = madrid['years_of_hosting'].fillna(np.mean(madrid['years_of_hosting']))

In [50]:
# impute london null values
london['host_response_rate'] = london['host_response_rate'].fillna(np.mean(london['host_response_rate']))
london['review_scores_rating'] = london['review_scores_rating'].fillna(np.mean(london['review_scores_rating']))
london['desc_len'] = london['desc_len'].fillna(np.mean(london['desc_len']))
london['name_len'] = london['name_len'].fillna(np.mean(london['name_len']))
london['years_since_lastreview'] = london['years_since_lastreview'].fillna(np.mean(london['years_since_lastreview']))
london['years_of_hosting'] = london['years_of_hosting'].fillna(np.mean(london['years_of_hosting']))

In [51]:
# impute paris null values
paris['host_response_rate'] = paris['host_response_rate'].fillna(np.mean(paris['host_response_rate']))
paris['review_scores_rating'] = paris['review_scores_rating'].fillna(np.mean(paris['review_scores_rating']))
paris['desc_len'] = paris['desc_len'].fillna(np.mean(paris['desc_len']))
paris['name_len'] = paris['name_len'].fillna(np.mean(paris['name_len']))
paris['years_since_lastreview'] = paris['years_since_lastreview'].fillna(np.mean(paris['years_since_lastreview']))
paris['years_of_hosting'] = paris['years_of_hosting'].fillna(np.mean(paris['years_of_hosting']))

#### One-hot-encoding

In [52]:
raw = pd.read_csv('../data/raw/us-train.csv')

In [53]:
train_cols = list(raw.property_type.unique())

In [54]:
# fix madrids property type column
madrid['property_type'] = madrid['property_type'].str.replace('Private room in ', '')
madrid['property_type'] = madrid['property_type'].str.replace('Shared room in ', '')
madrid['property_type'] = madrid['property_type'].str.replace('Entire ', '')
madrid['property_type'] = madrid['property_type'].str.replace('Room in ', '')
madrid['property_type'] = madrid['property_type'].str.title()
madrid['property_type'] = madrid['property_type'].str.replace('Serviced Apartment', 'Serviced apartment')
madrid['property_type'] = madrid['property_type'].str.replace('Bed And Breakfast', 'Bed & Breakfast')
madrid['property_type'] = madrid['property_type'].str.replace('Camper/Rv', 'Camper/RV')
madrid['property_type'] = madrid['property_type'].str.replace('Casa Particular', 'Casa particular')
madrid['property_type'] = madrid['property_type'].str.replace('Guest Suite', 'Guest suite')
madrid['property_type'] = madrid['property_type'].str.replace('Home/Apt', 'House')
madrid['property_type'] = madrid['property_type'].apply(lambda x: 'Other' if x not in train_cols else x)

In [55]:
# fix londons property type column
london['property_type'] = london['property_type'].str.replace('Private room in ', '')
london['property_type'] = london['property_type'].str.replace('Shared room in ', '')
london['property_type'] = london['property_type'].str.replace('Entire ', '')
london['property_type'] = london['property_type'].str.replace('Room in ', '')
london['property_type'] = london['property_type'].str.title()
london['property_type'] = london['property_type'].str.replace('Serviced Apartment', 'Serviced apartment')
london['property_type'] = london['property_type'].str.replace('Bed And Breakfast', 'Bed & Breakfast')
london['property_type'] = london['property_type'].str.replace('Camper/Rv', 'Camper/RV')
london['property_type'] = london['property_type'].str.replace('Casa Particular', 'Casa particular')
london['property_type'] = london['property_type'].str.replace('Guest Suite', 'Guest suite')
london['property_type'] = london['property_type'].str.replace('Home/Apt', 'House')
london['property_type'] = london['property_type'].apply(lambda x: 'Other' if x not in train_cols else x)

In [56]:
# fix paris property type column
paris['property_type'] = paris['property_type'].str.replace('Private room in ', '')
paris['property_type'] = paris['property_type'].str.replace('Shared room in ', '')
paris['property_type'] = paris['property_type'].str.replace('Entire ', '')
paris['property_type'] = paris['property_type'].str.replace('Room in ', '')
paris['property_type'] = paris['property_type'].str.title()
paris['property_type'] = paris['property_type'].str.replace('Serviced Apartment', 'Serviced apartment')
paris['property_type'] = paris['property_type'].str.replace('Bed And Breakfast', 'Bed & Breakfast')
paris['property_type'] = paris['property_type'].str.replace('Camper/Rv', 'Camper/RV')
paris['property_type'] = paris['property_type'].str.replace('Casa Particular', 'Casa particular')
paris['property_type'] = paris['property_type'].str.replace('Guest Suite', 'Guest suite')
paris['property_type'] = paris['property_type'].str.replace('Home/Apt', 'House')
paris['property_type'] = paris['property_type'].apply(lambda x: 'Other' if x not in train_cols else x)

In [57]:
cate_vari = ['property_type','room_type']
for i in cate_vari:
    madrid[i]=pd.Categorical(madrid[i])
    london[i]=pd.Categorical(london[i])
    paris[i]=pd.Categorical(paris[i])

In [58]:
#one hot encoding for categorical variables madrid
enc = OneHotEncoder(handle_unknown='ignore')
madrid_ohe = pd.DataFrame(enc.fit_transform(madrid[cate_vari]).toarray())
madrid_ohe.columns = enc.get_feature_names()
madrid = madrid.join(madrid_ohe)
madrid.drop(columns=cate_vari, inplace=True)
madrid.drop(columns=['x1_Hotel room'], inplace=True)

In [59]:
#one hot encoding for categorical variables london
enc = OneHotEncoder(handle_unknown='ignore')
london_ohe = pd.DataFrame(enc.fit_transform(london[cate_vari]).toarray())
london_ohe.columns = enc.get_feature_names()
london = london.join(london_ohe)
london.drop(columns=cate_vari, inplace=True)
london.drop(columns=['x1_Hotel room'], inplace=True)

In [60]:
#one hot encoding for categorical variables paris
enc = OneHotEncoder(handle_unknown='ignore')
paris_ohe = pd.DataFrame(enc.fit_transform(paris[cate_vari]).toarray())
paris_ohe.columns = enc.get_feature_names()
paris = paris.join(paris_ohe)
paris.drop(columns=cate_vari, inplace=True)
paris.drop(columns=['x1_Hotel room'], inplace=True)

#### Duplicate missing columns from train

In [87]:
train = pd.read_csv('../data/processed/us-train.csv')
train_cols = set(train.columns)

In [88]:
# fill madrid columns
missing_cols = list(train_cols - set(madrid.columns))
for col in missing_cols:
    madrid[col] = 0

In [89]:
# fill london columns
missing_cols = list(train_cols - set(london.columns))
for col in missing_cols:
    london[col] = 0

In [94]:
# fill paris columns
missing_cols = list(train_cols - set(paris.columns))
for col in missing_cols:
    paris[col] = 0

## Impute infs

For bed bath column when dividing by 0.

In [81]:
inf_list = [np.inf, -np.inf]

mode_bedbath = madrid['bed_bath_ratio'].mode()[0]
madrid['bed_bath_ratio'] = madrid['bed_bath_ratio'].apply(lambda x: mode_bedbath if x in inf_list else x)

mode_bedbath = london['bed_bath_ratio'].mode()[0]
london['bed_bath_ratio'] = london['bed_bath_ratio'].apply(lambda x: mode_bedbath if x in inf_list else x)

mode_bedbath = paris['bed_bath_ratio'].mode()[0]
paris['bed_bath_ratio'] = paris['bed_bath_ratio'].apply(lambda x: mode_bedbath if x in inf_list else x)

## Output cleaned files

In [91]:
madrid.to_csv('../data/processed/madrid-test.csv', index=False)

In [92]:
london.to_csv('../data/processed/london-test.csv', index=False)

In [95]:
paris.to_csv('../data/processed/paris-test.csv', index=False)